# Integration of the equations of motion



Now that we have forces defined, we need to have a method for integrating the equations of motion. Let's take a look of a few of them. Numerically, this is an initial value problem. There are several possible numerical integration methods, and all of the software packages have at least a few of them available. In general, there are several requirements for an algorithm, including

```{admonition} Requirements for numerical algorithms in MD
:class: tip
- The algorithm should not violate physical laws. 
- Algorithms should always be checked that don't violate conservation laws, for example energy, momentum (both linear and angular).
- The algorithm must be time-reversible.
- The algorithm should be symplectic (conservation of phase space volume).
- The algorithm should be fast.
- The algorithm should allow for a long time step.
- Ideally, the algorithm should also be (relatively) easy to program.

```

Below we discuss several algorithms and illustrate some of the points listed above. The list of algorithms below is by no means exhaustive and many others, especially predictor-corrector type algorithms exist for MD.

```{figure} ./img/integration.svg
---
width: 400px
align: left
---
Schematic showing integration. The system is propagate using a finite time step $\Delta t$.
```

<p></p>



## Euler algorithm

Let's start the discussion from an algorithm that one should not use, the forward Euler algorithm. The algorithm is very easy to derive, one simply Taylor expands both the position and the velocity in the forward direction,

\begin{align*}
\vec{r}_i(t + \Delta t) & = \vec{r}_i(t) + \frac{d\,\vec{r}_i(t)}{d\,t} \Delta t
 + \frac{1}{2}\frac{d^2\,\vec{r}_i(t)}{d\,t^2} (\Delta t)^2 \\
\vec{v}_i(t + \Delta t) & = \vec{v}_i(t) + \frac{d\,\vec{v}_i(t)}{d\,t} \Delta t
 + \frac{1}{2}\frac{d^2\,\vec{v}_i(t)}{d\,t^2} (\Delta t)^2
\end{align*}

Using $\vec{F} = m \vec{a} = m d^2\vec{r}(t) /dt^2 $, and dropping the second order term for velocity, we can write the above equations also as

\begin{align*}
%\left\{
\vec{r}_i(t + \Delta t) & = \vec{r}_i(t) + \vec{v}_i(t) \Delta t
 + \frac{\vec{F}_i(t)}{2m_i} (\Delta t)^2 \\
\vec{v}_i(t + \Delta t) & = \vec{v}_i(t) + \frac{\vec{F}_i(t)}{m_i} \Delta t
% + \frac{1}{2}\frac{d^2\,\vec{v}_i(t)}{d\,t^2} (\Delta t)^2
%\right.
\end{align*}

This also looks good, but let's investigate one of the requirements, namely, that the algorithm is time-reversal. This is easy to do: We simply propagate the system forward in time by $\Delta t$ and then propagate it backwards by $-\Delta t$ and we should arrive to the starting point, that is, we should obtain

\begin{align*}
r_\mathrm{b} (t_0) & = r_\mathrm{f}  (t_0) \\
v_\mathrm{b} (t_0) & = v_\mathrm{f}  (t_0). \\
\end{align*}

Let's test the above for the position using the time $t_0$ as the reference point. Let's use one the dimensional case and drop the particle indices ($i$) for notational convenience. Then, using the above equations, we have

\begin{align*}
% ok
r_\mathrm{b} ( t_0 +\Delta t - \Delta t) & = r_\mathrm{f}  (t_0 + \Delta t) 
+ v(t_0 + \Delta t) (-\Delta t) + \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2 \\
r_\mathrm{b} (t_0) & = r_\mathrm{f}  (t_0 + \Delta t) 
+ v(t_0 + \Delta t) (-\Delta t) + \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2   
\end{align*}

Substitute the expression from the above for $r_\mathrm{f}  (t_0 + \Delta t) $:
\begin{align*}
r_\mathrm{b} (t_0) & = 
\left[ 
r_\mathrm{f}(t_0) + v(t_0) \Delta t + \frac{F(t_0)}{2m} (\Delta t)^2   
\right] + v(t_0 + \Delta t) (-\Delta t) + \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2\\
%
%r_\mathrm{fw}  (t_0 + \Delta t) 
%+ v(t_0 + \Delta t) (-\Delta t) + \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2 \\
\end{align*}

and we do the same using $\vec{v}_i(t + \Delta t)$,
\begin{align*}
r_\mathrm{b} (t_0) & =r_\mathrm{f}(t_0) + \cancel{v(t_0) \Delta t} + \frac{F(t_0)}{2m} (\Delta t)^2 +
\left[ 
\cancel{v(t_0)} + \frac{F(t_0)}{m} \Delta t
\right]   (-\Delta t)
+ \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2\\
r_\mathrm{b} (t_0) & =r_\mathrm{f}(t_0) + \frac{F(t_0)}{2m} (\Delta t)^2 - \frac{F(t_0)}{m} (\Delta t)^2 + \frac{F(t_0 + \Delta t)}{2m} ( - \Delta t)^2\\
r_\mathrm{b} (t_0) & =r_\mathrm{f}(t_0)  + \frac{(\Delta t)^2}{2m}
\left[ F(t_0 + \Delta t) - F(t_0) \right] \\ 
\end{align*}

This clearly violates the requirement that $r_\mathrm{b} (t_0)  = r_\mathrm{f}  (t_0) $.

```{admonition} Properties of the forward Euler algorithm
:class: tip
- It is not time-reversible.
- The forward Euler algorithm doesn't conserve energy.
- Error (local) is $\mathcal{O}(\Delta  t^2)$
- Easy to derive.
- Illustrates well some problems with algorithms.
- Despite the problems, it is available in several software packages.
```

## Verlet algorithm

Unlike that forward Euler algorithm, the Verlet algorithm is well-behaved. The Verlet algorithm in MD is due to [Loup Verlet](https://www.cecam.org/news-details/loup-verlet), but the general algorithm goes back to 1791. The Verlet algorithm us not commonly used in MD simulations since in its basic forms, it propagates positions only. In it's essence, the Verlet algorithm is central difference approximation of the second derivative. 

The Verlet algorithm is obtained by addition of Taylor expanding the position $\vec{r}(t)$ twice and then adding the expansions. 

\begin{align*}
 \vec{r}(t + \Delta t) & = \vec{r}(t) + \frac{d\,\vec{r}(t)}{d\,t} \Delta t
 + \frac{1}{2}\frac{d^2\,\vec{r}(t)}{d\,t^2} (\Delta t)^2 + \frac{1}{3!}\frac{d^3\,\vec{r}(t)}{d\,t^3} (\Delta t)^3 
 +  \mathcal{O} ((\Delta t)^4) \\
  \vec{r}(t - \Delta t) & = \vec{r}(t) - \frac{d\,\vec{r}(t)}{d\,t} \Delta t
 + \frac{1}{2}\frac{d^2\,\vec{r}(t)}{d\,t^2} (\Delta t)^2 - \frac{1}{3!}\frac{d^3\,\vec{r}(t)}{d\,t^3} (\Delta t)^3 
 +  \mathcal{O} ((\Delta t)^4)
 %\dot{\vec{r}}(t) \Delta t + 
\end{align*}
If we now add the two expansions, we obtain
\begin{align*}
 \vec{r}(t + \Delta t) +  \vec{r}(t - \Delta t) & = 2 \vec{r}(t) + \frac{d^2\,\vec{r}(t)}{d\,t^2} (\Delta t)^2  +  \mathcal{O} ((\Delta t)^4) \\
  \vec{r}(t + \Delta t) &  =  2 \vec{r}(t) - \vec{r}(t - \Delta t) + \frac{d^2\,\vec{r}(t)}{d\,t^2} (\Delta t)^2  +  \mathcal{O} ((\Delta t)^4) \\
    \vec{r}(t + \Delta t) & =  2 \vec{r}(t) - \vec{r}(t - \Delta t) + \frac{\vec{F}}{m}  (\Delta t)^2  +  \mathcal{O} ((\Delta t)^4) 
\end{align*}
The last line was obtained by noticing that $\vec{F} = m \vec{a} = m d^2\vec{r}(t) /dt^2 $. The last term, $\mathcal{O} ((\Delta t)^4) $ means that the error is of order $(\Delta t)^4$.



To resolve the velocities that are needed for kinetic energy, one simply uses the central difference formula
\begin{equation}
\vec{v}_{i}(t)=\frac{\vec{r}_{i}(t+\Delta{t})-\vec{r}_{i}(t-\Delta{t})}{2\Delta{t}}.
\end{equation}
Note that the accuracy of velocity is not $(\Delta t)^4$ but $(\Delta t)^2$ instead.

```{admonition} Properties of the Verlet algorithm
:class: tip
- The Verlet algorithm has no explicit velocities, but velocities can be computed.
- It is easy to code, it's fast and doesn't require much memory.
- The symmetric expansion around  $\vec{r}(t)$ renders the algorithm time-reversible.
%- The error is of order $(\Delta t)^4$.
- It is energy conserving. Note that several of the other conservation laws cannot be checked as the Verlet algorithm doesn't have explicit velocities.

```


% about $\vec{r}(t)$ in two different time directions.
%It reads as follows
%\begin{equation}
%\vec{r}_{i}(t+\Delta{t})=2\vec{r}_{i}(t)-\vec{r}_{i}(t-\Delta{t})+\frac{1}{m}\vec{F}_{i}(t)(\Delta{t})^2.
%\end{equation}
%The Verlet algorithm uses the position and force at time $t$ and the position at time $(t-\Delta{t})$ to calculate the new position at %time $(t+\Delta{t})$. So at $t=0$ the position at time $(-\Delta{t})$ is needed. This problem is usually solved by using a Taylor %expansion about $\vec{r}(t)$.
%The velocity, which does not appear explicitly in the Verlet algorithm, can be obtained from the finite difference formula
%\begin{equation}
%\vec{v}_{i}(t)=\frac{\vec{r}_{i}(t+\Delta{t})-\vec{r}_{i}(t-\Delta{t})}{2\Delta{t}}
%\end{equation}
%In this algorithm the velocity term is always a step behind the position term.


## Leapfrog algorithm

The leapfrog algorithm is based on the Verlet algorithm. It adds explicit velocities to the Verlet algorithm. The name *leapfrog* comes from the fact that in this algorithm, the positions and velocities are half time step off from each other, that is, they are *leapfrogging* each other. Leapfrog is included as an integration algorithm in most simulation packages. The algorithm is mathematically equivalent to the Verlet algorithm

\begin{eqnarray}
\vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right) &=& \vec{v}_{i}\left(t-\frac{\Delta{t}}{2}\right)+ \vec{a}_{i}(t)\Delta{t} \nonumber\\
\vec{r}_{i}(t+\Delta{t}) &=& \vec{r}_{i}(t)+\vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right)\Delta{t} \nonumber\\
\end{eqnarray}

Velocities at the full time step are obtained analogously as what is done in the basic Verlet algorithm, 

\begin{equation}
\vec{v}_{i}=\frac{\vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right)+\vec{v}_{i}\left(t-\frac{\Delta{t}}{2}\right)}{2}.
\end{equation}

```{prf:algorithm} The leapfrog algorithm
:label: leapfrog-algorithm

1. Initialize: Need initial values ($t=t_0$) for $\vec{r}_i$ and $\vec{v}_i$.
   - Compute the forces (accelerations) using the interaction potentials and the initial values for the positions. That gives $ \vec{a}_i(t_0)$.
   - With the above we have $\vec{r}_i(t=t_0)$, $\vec{v}_i(t=t_0)$ and $\vec{a}_i(t=t_0)$.

```



```{admonition} Properties of the leapfrog algorithm
:class: tip
- Has explicit velocities, but the velocties and positions are not computed at the same step.
- It is easy to code and it is fast.
- The symmetric expansion around  $\vec{r}(t)$ renders the algorithm time-reversible.
- It is energy conserving.
- The error is of order $(\Delta t)^2$ for moment and $(\Delta t)^2$ for positions.
- In the Verlet algorithm the velocity term is a step behind the position term, that is, it is not self-starting as it needs initialization for $x(t- \Delta t)$.
```


## Velocity-Verlet

The velocity-Verlet algorithm is one of the most commonly used MD algorithms and it is available in essentially all software packages. It fulfills the requirements listed at the beginning of this section. As the name suggests, it is based on the Verlet algorithm and adds explicit velocities. It is also worth noticing that mathematically the velocity-Verlet algorithm is identical to the Verlet algorithm

```{prf:algorithm} Velocity-Verlet
:label: vv-algorithm

1. Initialize: Need initial values ($t=t_0$) for $\vec{r}_i$ and $\vec{v}_i$.
   - Compute the forces (accelerations) using the interaction potentials and the initial values for the positions. That gives $ \vec{a}_i(t_0)$.
   - With the above we have $\vec{r}_i(t=t_0)$, $\vec{v}_i(t=t_0)$ and $\vec{a}_i(t=t_0)$.
1. Loop over time. At each step:
   1. Compute half-step velocities: $\vec{v}_i(t + \frac{\Delta t}{2}) = \vec{v}_i(t) + \frac{1}{2} \vec{a}_i(t) \Delta t$.
   2. Compute the (full step) positions: $ \vec{r}_i(t + \Delta  t) = \vec{r}_i(t) + \vec{v}_i (t+\frac{\Delta t}{2}) \Delta t$.
   3. Compute the forces (accelerations) using the interaction potential. That gives $ \vec{a}_i(t + \Delta  t)$.
   4. Update the velocities (full-step): $ \vec{v}_i(t + \Delta t) =  \vec{v}_i (t+\frac{\Delta t}{2}) + \frac{1}{2} \vec{a}_i(t + \Delta t) \Delta t$.
```

```{admonition} Properties of the velocity-Verlet algorithm
:class: tip
- It is time reversible and symplectic.
- Very stable.
- It is easy to code. At the end of the integration step, all the positions and velocities are at the same time.
%- The error is of order $(\Delta t)^4$.
- Possibly the  most used MD simulation algorithm. 
```


%## Algorithms in software packages
%
%- Gromacs has currently the following algorithms:
%   - leap frog, velocity-Verlet, velocity-Verlet with the kinetic energy calculated as an average of two half-step $E_\mathrm{kin}$, (leap frog) stochastic dynamics integrator, Euler integrator
%- NAMD has:
%    - Velocity-Verlet

%## Trotter expansion

%The method described here is a great tool to develop algorithms from equations of motion. Especially for complex systems it is hard to %find a scheme, which is symplectic, i.e. preserves volume in phase space and the growth in the error of energy conservation is %bounded. Examples of algorithms found by this method are the reversible reference system propagator (r-RESPA) technique [45, 46], a 
%multiple time-step (MTS) integration method, or a symplectic algorithm to implement the Nose-Hoover Chain equations (see below) to 
%simulate the NVT ensemble [47]. As an illustrative example the method for a Hamiltonian system is described below.

%By introducing the phase space vector $\vec{x}(\left\{\vec{p}_{i}\right\},\left\{\vec{r}_{i}\right\}), i=1,..,N$ for a system %consisting of $N$ particles, where all the momenta $\vec{p}\equiv\vec{p}_{1},...,\vec{p}_{N}$ and coordinates $\vec{r}\equiv\vec{r}_{1},...,\vec{r}_{N}$ are collected, Newton's equation of motion in the formulation of first order differential equations (eq \ref{eq:Newton}) can be written in the form of an operator equation
%\begin{equation}
%\dot{\vec{x}}=iL\vec{x}
%\end{equation}
%where the $iL$ is a generalization of the Liouville operator, which has the formal solution
%\begin{equation}
%\vec{x}(t)=\exp(iLt)\vec{x}(0).
%\end{equation}
%In a Hamiltonian system with the following Hamiltonian 
%\begin{equation}
%\mathcal{H}(\left\{\vec{p}_{i}\right\},\left\{\vec{r}_{i}\right\})=\sum\limits_{i=1}^N\frac{\vec{p}_{i}^{2}}{2m_{i}}+U(\left\{\vec{r}_{i}\right\})
%\end{equation}
%the Liouville operator becomes
%\begin{eqnarray} 
%iL &=& \sum\limits_{i=1}^N\left[ \frac{\partial\mathcal{H}}{\partial\vec{p}_{i}}\cdot\frac{\partial}{\partial\vec{r}_{i}}-\frac{\partial\mathcal{H}}{\partial\vec{r}_{i}}\cdot\frac{\partial}{\partial\vec{p}_{i}}\right] 
%=\sum\limits_{i=1}^N\frac{\vec{p}_{i}}{m_{i}}\cdot\frac{\partial}{\partial\vec{r}_{i}}+\sum\limits_{i=1}^N\vec{F}_{i}\cdot\frac{\partial}{\partial\vec{p}_{i}} \nonumber \\
%&=& \sum\limits_{i=1}^N\dot{\vec{r}}_{i}\cdot\frac{\partial}{\partial\vec{r}_{i}}+\sum\limits_{i=1}^N\dot{\vec{p}}_{i}\cdot\frac{\partial}{\partial\vec{p}_{i}}
%\equiv{iL_{1}+iL_{2}}. \nonumber \\
%\end{eqnarray}
%The formal solution can be determined only for a few simple cases explicitly, for example for the assumption $iL=iL_{1}$ or $iL=iL_{2}$. If
%\begin{equation}
%iL=iL_{1}=\sum\limits_{i=1}^N\dot{\vec{r}}_{i}(0)\cdot\frac{\partial}{\partial\vec{r}_{i}}
%\end{equation}
%is inserted into the formal solution and a Taylor expansion is used, the following result is found
%\begin{eqnarray}
%\vec{x}(t) &=& \exp\left(iL_{1}t\right)\vec{x}(0)=\exp\left(\sum\limits_{i=1}^N\dot{\vec{r}}_{i}t\frac{\partial}{\partial\vec{r}_{i}}\right)\vec{x}(0) \nonumber\\
%&=& \vec{x}(0)+iL_{1}t\vec{x}(0)+\frac{\left(iL_{1}\right)^2}{2!}\vec{x}(0)+... \nonumber\\
%&=& \sum\limits_{n=0}^{\infty}\left(\sum\limits_{i=1}^N\left(\frac{\left(\dot{\vec{r}}_{i}(0)t\right)^n}{n!}\frac{\partial{^n}}{\partial\vec{r}_{i}^n}\right)\vec{x}(0)\right) \nonumber\\
%&=& x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\left(\vec{r}_{i}+\dot{\vec{r}}_{i}(0)t\right)\right\}\right] \nonumber\\
%\end{eqnarray}
%Hence the application of $\exp(iL_{1}t)$ effects in a simple shift of the coordinates. It can be shown in the same way that the application of $\exp(iL_{2})$, %where 
%\begin{equation}
%iL_{2}=\sum\limits_{i=1}^N\dot{\vec{p}}(0)\cdot\frac{\partial}{\partial\vec{p}_{i}}
%\end{equation}
%leads to a simple shift in the momenta.
%Now to find the effect of the total Liouville operator the Trotter theorem [48, 49] can be used, which states
%\begin{eqnarray}
%\exp(iLt) &=&\exp\left[(iL_{1}+iL_{2})t\right] \nonumber\\
%&=& \lim\limits_{P\rightarrow\infty}\left[\exp\left(\frac{iL_{2}t}{2P}\right)\exp\left(\frac{iL_{1}t}{P}\right)\exp\left(\frac{iL_{2}t}{2P}\right)\right]^P. %\nonumber\\
%\end{eqnarray}
%Defining $\frac{t}{p}=\Delta{t}$ for finite and large $P$ leads to the following approximation [50]
%\begin{eqnarray}
%\exp(iL\Delta{t})&\approx&\left[\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)\exp\left(iL_{1}\Delta{t}\right)\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)\right]+\mathcal{O}(\Delta{t}^3) \nonumber\\
%\exp(iLP\Delta{t})&\approx&\prod\limits_{k=1}^P\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)\exp(iL_{1}\Delta{t})\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)+\mathcal{O}(t\Delta{t}^2) \nonumber\\
%\end{eqnarray}
%and the formal solution of the Liouville equation can be replaced by a discretized scheme, by using the above approximation. 
%Hence by applying the operator $\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)\exp(iL_{1}\Delta{t})\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)$ the system advances one %time step. The application of this operator can be broken down into three steps.
%In the first step $\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)$ is applied to $x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\vec{r}_{i}(0)\right\}\right]$ and the %result is
%\begin{eqnarray} \label{eq:Liouv1}
%\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\vec{r}_{i}(0)\right\}\right] \nonumber\\
%=x\left[\left\{\left(\vec{p}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(0)\right)\right\},\left\{\vec{r}_{i}(0)\right\}\right]. \nonumber\\
%\end{eqnarray}
%In the second step $\exp\left(iL_{1}\Delta{t}\right)$  is applied to the result above (eq \ref{eq:Liouv1}) and the following expression results
%\begin{eqnarray}
%\exp\left(iL_{1}\Delta{t}\right)x\left[\left\{\left(\vec{p}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(0)\right)\right\},\left\{\vec{r}_{i}(0)\right\}\right] %\nonumber\\
%=x\left[\left\{\left(\vec{p}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(0)\right)\right\},\left\{\left(\vec{r}_{i}(0)+\Delta{t}\dot{\vec{r}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\}\right]. \nonumber\\
%\end{eqnarray}
% In the last step $\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)$ is applied once again, which leads to the following final expression for this time step
%\begin{eqnarray}
%\exp\left(iL_{2}\frac{\Delta{t}}{2}\right)x\left[\left\{\left(\vec{p}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(0)\right)\right\},\left\{\left(\vec{r}_{i}(0)+\Delta{t}\dot{\vec{r}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\}\right] \nonumber\\
%=x\left[\left\{\left(\vec{p}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{p}}_{i}(\Delta{t})\right)\right\},\left\{\left(\vec{r}_{i}(0)+\Delta{t}\dot{\vec{r}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\}\right]. \nonumber\\
%\end{eqnarray}
%The total effect of applying this operator to the coordinates and the momenta can be summarized as
%\begin{eqnarray}
%\vec{p}_{i}(0) &\rightarrow& \vec{p}_{i}(0)+\frac{\Delta{t}}{2}\left(\vec{F}_{i}(0)+\vec{F}_{i}(\Delta{t})\right) \nonumber\\
%\vec{r}_{i}(0) &\rightarrow& \vec{r}_{i}(0)+\Delta{t}\dot{\vec{r}}_{i}\left(\frac{\Delta{t}}{2}\right) \nonumber\\
%&=& \vec{r}_{i}(0)+\Delta{t}\dot{\vec{r}}_{i}(0)+\frac{\Delta{^2}t}{2m_{i}}\vec{F}_{i}(0), \nonumber\\
%\end{eqnarray}
%which is equal to the Velocity Verlet algorithm [41] defined as
%\begin{eqnarray}
%\vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right) &=& \vec{v}_{i}(t)+\frac{1}{2m_{i}}\vec{F}_{i}(t)\Delta{t} \nonumber\\
%\vec{r}_{i}\left(t+\Delta{t}\right) &=& \vec{r}_{i}(t)+\vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right)\Delta{t} \nonumber\\
%\vec{v}_{i}\left(t+\Delta{t}\right) &=& \vec{v}_{i}\left(t+\frac{\Delta{t}}{2}\right)+\frac{1}{2m_{i}}\vec{F}_{i}\left(t+\Delta{t}\right)\Delta{t}. \nonumber\\
%\end{eqnarray}
%Switching the terms in the sum of the Liouville operator and using the Trotter theorem [48, 49] again leads to
%\begin{eqnarray}
%\exp(iLt) &=& \exp\left[(iL_{2}+iL_{1})t\right]  \nonumber\\
%&=& \lim\limits_{P\rightarrow\infty}\left[\exp\left(\frac{iL_{1}t}{2P}\right)\exp\left(\frac{iL_{2}t}{P}\right)\exp\left(\frac{iL_{1}t}{2P}\right)\right]^P. %\nonumber\\
%\end{eqnarray}
%and by again defining $\frac{t}{p}=\Delta{t}$ the following approximation is found for finite and large $P$ [50]
%\begin{eqnarray}
%\exp(iL\Delta{t})&\approx&\left[\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)\exp\left(iL_{2}\Delta{t}\right)\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)\right]+\mathcal{O}(\Delta{t}^3) \nonumber\\
%\exp(iLP\Delta{t})&\approx&\prod\limits_{k=1}^P\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)\exp(iL_{2}\Delta{t})\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)+\mathcal{O}%(t\Delta{t}^2) \nonumber\\
%\end{eqnarray}
%So the operator that needs to be applied to advance the system by a time step in this case is $\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)\exp(iL_{2}\Delta{t})\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)$.
%Again the application of this operator can be broken down into three steps.
%First $\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)$ is applied to $x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\vec{r}_{i}(0)\right\}\right]$ resulting
%\begin{eqnarray} \label{eq:Liouv2}
%\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\vec{r}_{i}(0)\right\}\right] \nonumber\\
%=x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\left(\vec{r}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(0)\right)\right\}\right] \nonumber\\
%\end{eqnarray}
%Next $\exp(iL_{2}\Delta{t})$ is applied to eq \ref{eq:Liouv2}
%\begin{eqnarray}
%\exp(iL_{2}\Delta{t})x\left[\left\{\vec{p}_{i}(0)\right\},\left\{\left(\vec{r}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(0)\right)\right\}\right] \nonumber\\
%=x\left[\left\{\left(\vec{p}_{i}(0)+\Delta{t}\dot{\vec{p}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\},\left\{\left(\vec{r}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(0)\right)\right\}\right]. \nonumber\\
%\end{eqnarray}
%Last $\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)$ is applied once again and the final expression for this time step is obtained
%\begin{eqnarray}
%\exp\left(iL_{1}\frac{\Delta{t}}{2}\right)x\left[\left\{\left(\vec{p}_{i}(0)+\Delta{t}\dot{\vec{p}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\},\left\{\left(\vec{r}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(0)\right)\right\}\right] \nonumber\\
%=x\left[\left\{\left(\vec{p}_{i}(0)+\Delta{t}\dot{\vec{p}}_{i}\left(\frac{\Delta{t}}{2}\right)\right)\right\},\left\{\left(\vec{r}_{i}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(0)+\frac{\Delta{t}}{2}\dot{\vec{r}}(\Delta{t})\right)\right\}\right]. \nonumber\\
%\end{eqnarray}
%The total effect of applying this operator is
%\begin{eqnarray}
%\vec{p}_{i}(0) &\rightarrow& \vec{p}_{i}(0)+\Delta{t}\vec{F}_{i}\left(\frac{\Delta{t}}{2}\right) \nonumber\\
%\vec{r}_{i}(0) &\rightarrow& \vec{r}_{i}(0)+\frac{\Delta{t}}{2}\left[\dot{\vec{r}}_{i}(0)+\dot{\vec{r}}_{i}(\Delta{t})\right] \nonumber\\
%&=& \vec{r}_{i}(0)+\Delta{t}\vec{v}_{i}(0)+\frac{\Delta{^2}t}{2m_{i}}\vec{F}_{i}\left(\frac{\Delta{t}}{2}\right). \nonumber\\
%\end{eqnarray}
%These equations are equal the position Verlet algorithm [51-53] defined as
%\begin{eqnarray} \label{eq:posver}
%\vec{r}_{i}\left(t+\frac{\Delta{t}}{2}\right) &=& \vec{r}_{i}(t)+\frac{\Delta{t}}{2}\vec{v}_{i}(t) \nonumber\\
%\vec{v}_{i}\left(t+\Delta{t}\right) &=& \vec{v}_{i}(t)+\frac{1}{m}\vec{F}_{i}\left(t+\frac{\Delta{t}}{2}\right)\Delta{t} \nonumber\\
%\vec{r}_{i}\left(t+\Delta{t}\right) &=& \vec{r}_{i}\left(t+\frac{\Delta{t}}{2}\right)+\frac{\Delta{t}}{2}\vec{v}_{i}\left(t+\Delta{t}\right). \nonumber\\
%\end{eqnarray}

%The application of each operator as one step can easily be turned into instructions in a computer code. This direct translation %technique is very useful in more complex systems, e.g. for non-Hamiltonian or quantum systems.

%A transformation from the original phase point $\vec{x}_{0}$ to the phase point a time step later $\vec{x}_{\Delta{t}}$ is a %symplectic transformation if and only if it satisfies
%\begin{equation} \label{eq:transform}
%J^TTJ=T,
%\end{equation}
%where $J$ is the Jacobian
%\begin{equation}
%J=\left| \begin{array}{cc}
%\frac{\partial(r_{\Delta{t}}^1,...,r_{\Delta{t}}^n)}{\partial(r_{0}^1,...,r_{0}^n)}  & \frac{\partial(r_{\Delta{t}}^1,...,r_{\Delta{t}}%^n)}{\partial(p_{0}^1,...,p_{0}^n)}  \\
%\frac{\partial(p_{\Delta{t}}^1,...,p_{\Delta{t}}^n)}{\partial(r_{0}^1,...,r_{0}^n)}  & \frac{\partial(p_{\Delta{t}}^1,...,p_{\Delta{t}}%^n)}{\partial(p_{0}^1,...,p_{0}^n)}\end{array} \right|.
%\end{equation}
%and $T$ is the $6N$ dimensional matrix
%\begin{equation}
%T=\left( \begin{array}{ccc}
%0 & I  \\
%-I & 0\end{array} \right).
%\end{equation}
%where $I$ is the $3N\times3N$ identity matrix. For the velocity and position Verlet integtor, the Jacobian of the transformation for a %time step is the $6N\times6N$ identity matrix, which satisfies eq \ref{eq:transform} and these integrators are therefore symplectic.


%### Velocity-Verlet using Trotter expansion
%
%### Position-Verlet using Trotter expansion